In [1]:
# coding=utf-8
from hpsklearn import HyperoptEstimator, any_classifier, any_preprocessing, any_regressor
import pandas as pd
import warnings
from hyperopt import tpe
import numpy as np
# from auto_ml.tools.conn_try_again import conn_try_again
# from auto_ml.tools.typeassert import typeassert
import copy
# from auto_ml.core.parameter_parser import Parser
from sklearn.model_selection import train_test_split
from core import ModelBuilder


import pandas as pd
from fbprophet import Prophet
import warnings
from datetime import date
import calendar
import os
import logging
logging.getLogger().setLevel(logging.DEBUG)
# warnings.filterwarnings('ignore')

%matplotlib inline

WARN: OMP_NUM_THREADS=None =>
... If you are using openblas if you are using openblas set OMP_NUM_THREADS=1 or risk subprocess calls hanging indefinitely


ERROR:fbprophet:Importing plotly failed. Interactive plots will not work.
DEBUG:matplotlib.backends:backend module://ipykernel.pylab.backend_inline version unknown
DEBUG:matplotlib.backends:backend module://ipykernel.pylab.backend_inline version unknown


In [2]:
 def iris_test_dataset():
        from sklearn.datasets import load_iris
        iris = load_iris()

        X = iris.data
        y = iris.target

        test_size = int(0.3 * len(y))
        np.random.seed(173)
        indices = np.random.permutation(len(X))
        X_train = X[indices[:-test_size]]
        y_train = (y[indices[:-test_size]]>1)*1
        X_test = X[indices[-test_size:]]
        y_test = (y[indices[-test_size:]]>1)*1

        dataset_dict = dict(X_train=X_train, X_test=X_test, y_train=y_train, y_test=y_test)
        return dataset_dict

In [3]:
# dataset_dict = iris_test_dataset()
# param=dict(classifier=None,
#            preprocessing=[], 
#            max_evals=20, 
#            trial_timeout=100)


# estim = ModelBuilder.create_estimator(param,param_type='clf')

# estim.fit(dataset_dict['X_train'],dataset_dict['y_train'])

# print('train',estim.score(dataset_dict['X_train'],dataset_dict['y_train']))

# print('test',estim.score(dataset_dict['X_test'],dataset_dict['y_test']))
# 
# estim.score(dataset_dict['X_test'],dataset_dict['y_test'])

In [4]:
train_sales_data = pd.read_csv('/Users/sn0wfree/PycharmProjects/auto_ml/data/Train/train_sales_data.csv')
train_search_data= pd.read_csv('/Users/sn0wfree/PycharmProjects/auto_ml/data/Train/train_search_data.csv')
train_user_reply_data= pd.read_csv('/Users/sn0wfree/PycharmProjects/auto_ml/data/Train/train_user_reply_data.csv')

evaluation_public = pd.read_csv('/Users/sn0wfree/PycharmProjects/auto_ml/data/evaluation_public.csv')

submit_example = pd.read_csv('/Users/sn0wfree/PycharmProjects/auto_ml/data/submit_example.csv')



In [6]:
df1 = pd.merge(train_sales_data,train_search_data,on=['model','province','adcode','regYear','regMonth'])
df2 = pd.merge(df1,train_user_reply_data)[[ 'province' , 'model', 'regYear', 'regMonth',
       'salesVolume', 'popularity', 'carCommentVolum', 'newsReplyVolum']]

dataset = pd.get_dummies(df2)

# dataset = pd.concat([dataset,pd.get_dummies(df2['adcode'],prefix='adcode')],axis=1)

# del dataset['adcode']
# dataset.head()

x = list(set(dataset.columns)-set(['salesVolume']))

y = ['salesVolume']

In [8]:
def run_it(param,param_type,dataset_dict,retry_count=5,valid_size=0.3,warm_start=False):
    try:
        estim = ModelBuilder.create_estimator(param,param_type='rgs')
        estim.fit(dataset_dict['X_train'],dataset_dict['y_train'],valid_size=valid_size,warm_start=warm_start)
    except (AttributeError,ValueError) as e:
        if retry_count>0:
            warnings.warn(f'will {retry_count} retry')
            retry_count -=1
            return run_it(param,param_type,dataset_dict,retry_count=retry_count)
        else:
            raise AttributeError(e)
    else:
        return estim
    
    

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(dataset[x],dataset[y],test_size=0.3)
dataset_dict = dict(X_train=X_train.values, 
                    X_test=X_test.values, 
                    y_train=y_train.values.ravel(), 
                    y_test=y_test.values.ravel())

param=dict(regressor=None,
           preprocessing=[], 
           max_evals=20, 
           trial_timeout=100)


# estim = ModelBuilder.create_estimator(param,param_type='rgs')

# estim.fit(dataset_dict['X_train'],dataset_dict['y_train'])
estim = run_it(param,'rgs',dataset_dict,retry_count=5)
print('train',estim.score(dataset_dict['X_train'],dataset_dict['y_train']))

print('test',estim.score(dataset_dict['X_test'],dataset_dict['y_test']))

  0%|          | 0/1 [00:00<?, ?it/s, best loss: ?]

INFO:hyperopt.tpe:tpe_transform took 0.037188 seconds
INFO:hyperopt.tpe:TPE using 0 trials


In [10]:
def get_result(estim,dataset_dict):
    model = estim.best_model()
    model['best_train_score']=estim.score(dataset_dict['X_train'],dataset_dict['y_train'])
    model['best_test_score']=estim.score(dataset_dict['X_test'],dataset_dict['y_test'])
    return model

In [13]:
model=get_result(estim,dataset_dict)
model

{'learner': RandomForestRegressor(bootstrap=False, criterion='mse', max_depth=None,
            max_features=0.25866624499022495, max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=208, n_jobs=1,
            oob_score=False, random_state=1, verbose=False,
            warm_start=False),
 'preprocs': (),
 'ex_preprocs': (),
 'best_train_score': 0.999999989907225,
 'best_test_score': 0.8807492905306323}

In [11]:
def EMA2(c, N, denominator=1):
    if N >= 1:
        if denominator == 1:
            denominator = sum(range(N + 1))
        return N / denominator * c[-1] + EMA2(c[len(c) - N:len(c) - 1], N - 1, denominator)
    else:
        return 0
EMA2([6,5,6,7,8,6,7,8,9,9,8,9],2)

8.666666666666666

In [12]:
pd.DataFrame(df2.groupby(['province','model','regYear','regMonth'])['carCommentVolum'].mean()).reset_index()

province             model  regYear  regMonth  carCommentVolum
0           上海  02aab221aabc03b9     2016         1              132
1           上海  02aab221aabc03b9     2016         2              160
2           上海  02aab221aabc03b9     2016         3              357
3           上海  02aab221aabc03b9     2016         4              243
4           上海  02aab221aabc03b9     2016         5              283
5           上海  02aab221aabc03b9     2016         6              252
6           上海  02aab221aabc03b9     2016         7              557
7           上海  02aab221aabc03b9     2016         8              652
8           上海  02aab221aabc03b9     2016         9              506
9           上海  02aab221aabc03b9     2016        10              649
10          上海  02aab221aabc03b9     2016        11              436
11          上海  02aab221aabc03b9     2016        12              361
12          上海  02aab221aabc03b9     2017         1              375
13          上海  02aab221aabc03b9     2017         2              483
14          上海  02aab221aabc03b9     2017         3              848
15          上海  02aab221aabc03b9     2017         4              380
16          上海  02aab221aabc03b9     2017         5              554
17          上海  02aab221aabc03b9     2017         6              310
18          上海  02aab221aabc03b9     2017         7              626
19          上海  02aab221aabc03b9     2017         8              843
20          上海  02aab221aabc03b9     2017         9             1058
21          上海  02aab221aabc03b9     2017        10              784
22          上海  02aab221aabc03b9     2017        11              608
23          上海  02aab221aabc03b9     2017        12              403
24          上海  04e66e578f653ab9     2016         1                6
25          上海  04e66e578f653ab9     2016         2                6
26          上海  04e66e578f653ab9     2016         3                4
27          上海  04e66e578f653ab9     2016         4               11
28          上海  04e66e578f653ab9     2016         5               21
29          上海  04e66e578f653ab9     2016         6               18
...        ...               ...      ...       ...              ...
31650      黑龙江  fde95ea242abd896     2017         7               93
31651      黑龙江  fde95ea242abd896     2017         8              129
31652      黑龙江  fde95ea242abd896     2017         9              107
31653      黑龙江  fde95ea242abd896     2017        10               68
31654      黑龙江  fde95ea242abd896     2017        11              139
31655      黑龙江  fde95ea242abd896     2017        12               81
31656      黑龙江  feabbf46658382b9     2016         1               70
31657      黑龙江  feabbf46658382b9     2016         2              123
31658      黑龙江  feabbf46658382b9     2016         3              167
31659      黑龙江  feabbf46658382b9     2016         4              205
31660      黑龙江  feabbf46658382b9     2016         5              224
31661      黑龙江  feabbf46658382b9     2016         6              253
31662      黑龙江  feabbf46658382b9     2016         7              193
31663      黑龙江  feabbf46658382b9     2016         8              284
31664      黑龙江  feabbf46658382b9     2016         9              213
31665      黑龙江  feabbf46658382b9     2016        10              297
31666      黑龙江  feabbf46658382b9     2016        11              381
31667      黑龙江  feabbf46658382b9     2016        12              588
31668      黑龙江  feabbf46658382b9     2017         1              239
31669      黑龙江  feabbf46658382b9     2017         2              266
31670      黑龙江  feabbf46658382b9     2017         3              457
31671      黑龙江  feabbf46658382b9     2017         4              305
31672      黑龙江  feabbf46658382b9     2017         5              260
31673      黑龙江  feabbf46658382b9     2017         6              757
31674      黑龙江  feabbf46658382b9     2017         7             1133
31675      黑龙江  feabbf46658382b9     2017         8             1604
3167

In [13]:
f = lambda x :pd.to_datetime("{x}/{y}".format(x=x[0],y=x[1]), format="%Y/%m").strftime('%Y-%m')

In [14]:
df2['ym'] = list(map(f,df2[['regYear','regMonth']].values))

In [15]:
# pd.DataFrame(df2.groupby(['province','model','ym'])['carCommentVolum'].mean()).reset_index().set_index(['ym']).plot()

###  ------------

In [16]:
from fbprophet import Prophet



In [17]:
class ProphetPredit:
    def __init__(self,Train,y,Submit):
        self.Train = Train
        self.Submit  = Submit
        self.Holiday = pd.DataFrame({
            "holiday":["NewYear","Spring","Labour","National","NewYear","Spring"],
            "ds":[date(2017,1,31),date(2017,2,28),date(2017,5,31),date(2017,10,30),date(2018,1,31),date(2018,2,28)],
            "lower_window":-1,
            "upper_window":1
        })
        self.y = y
    def GetData(self,province,model):
        data = self.Train[(self.Train["province"] == province) & (self.Train["model"] == model)]
        data["ds"] = data[["regYear", "regMonth"]].apply(lambda x: date(x["regYear"], x["regMonth"], calendar.monthrange(x["regYear"],x["regMonth"])[1]), axis=1)
        data["y"]  = data[self.y]
        return data
        
    def GetPredict(self,province,model):
        m = Prophet(holidays=self.Holiday)
        m.add_country_holidays(country_name="CN")
        data = self.GetData(province,model)
        m.fit(data[["ds", "y"]])
        future = m.make_future_dataframe(periods=4, freq="M")
        forecast = m.predict(future)
        score = forecast[['ds', 'yhat', 'yhat_lower', 'yhat_upper']].tail(4)
        score["score"] = score["yhat_upper"] * 0.6 + score["yhat_lower"] * 0.4
        score["regYear"] = score["ds"].apply(lambda x: x.year)
        score["regMonth"] = score["ds"].apply(lambda x: x.month)
        for month in score["regMonth"].unique():
#             round(score["score"][score["regMonth"]==month].values[0],0)
            self.Submit.loc[(self.Submit["province"]==province) & (self.Submit["model"]==model) & (self.Submit["regMonth"]==month),self.y] = round(score["score"][score["regMonth"]==month].values[0],0)
        print(f"{province} {model} Predict Done Result:{round(score['score'][score['regMonth']==month].values[0],0)}......")

    def main(self):
        province = self.Train["province"].unique()
        model = self.Train["model"].unique()
        for Province in province:
            for Model in model:
                self.GetPredict(Province,Model)
        return self.Submit



        
    

In [18]:
def boost_up(func,tasks,core=None,star=True):
    from multiprocessing import Pool
    if star:
            attribute = 'starmap'
    else:
            attribute = 'map'    
    
    with Pool(core) as p:  
        res = getattr(p,attribute)(func,tasks)
    return res



In [19]:
class DoProphet(object):
    @staticmethod
    def do_Prophet(data,province,model,y,Holiday,periods):
        data["ds"] = data[["regYear", "regMonth"]].apply(lambda x: date(x["regYear"], x["regMonth"], calendar.monthrange(x["regYear"],x["regMonth"])[1]), axis=1)
        data["y"]  = data[y]
        m = Prophet(holidays=Holiday)
        m.add_country_holidays(country_name="CN")
        m.fit(data[["ds", "y"]])
        future = m.make_future_dataframe(periods=periods, freq="M")
        forecast = m.predict(future)
        score = forecast[['ds', 'yhat', 'yhat_lower', 'yhat_upper']].tail(periods)
        score["score"] = score["yhat_upper"] * 0.6 + score["yhat_lower"] * 0.4
        score["regYear"] = score["ds"].apply(lambda x: x.year)
        score["regMonth"] = score["ds"].apply(lambda x: x.month)
        score2 = score[['regYear','regMonth','score']].rename(columns={'score':y})
        score2['province']=province
        score2['model']=model
        return score2
    
    @staticmethod
    def holiday():
        Holiday = pd.DataFrame({
            "holiday":["NewYear","Spring","Labour","National","NewYear","Spring"],
            "ds":[date(2017,1,31),date(2017,2,28),date(2017,5,31),date(2017,10,30),date(2018,1,31),date(2018,2,28)],
            "lower_window":-1,
            "upper_window":1
        })
        return Holiday
    
    @classmethod
    def prepare_tasks(cls, Train,y,period=4):
        tasks = [(data,province,model,y,cls.holiday(),period)  for (province,model), data in Train.groupby(['province','model']) ] 
        return tasks
    
    @classmethod
    def do_prophet(cls,Train,y,period=4):
        tasks = cls.prepare_tasks(Train,y,period=period)
        res = boost_up(DoProphet.do_Prophet,tasks,star=True)
        return pd.concat(res)


        



    

In [20]:

y = 'carCommentVolum'

Train = df2

Submit = evaluation_public


carCommentVolum = DoProphet. do_prophet(df2,'carCommentVolum')   

newsReplyVolum = DoProphet. do_prophet(df2,'newsReplyVolum')   

popularity = DoProphet. do_prophet(df2,'popularity')
salesVolume = DoProphet. do_prophet(df2,'salesVolume')

INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_s

INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_chang

INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override 

INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run

INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_chang

...

INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run p

INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run

INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:Disabli

INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run p

INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
INFO:fbprophet:n_changepoints greater than number of observations.Using 18.
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run

In [34]:
popularity['popularity']=popularity['popularity'].astype(int)
popularity.to_csv('popularity.csv')


newsReplyVolum['newsReplyVolum']=newsReplyVolum['newsReplyVolum'].astype(int)
carCommentVolum['carCommentVolum']=carCommentVolum['carCommentVolum'].astype(int)

carCommentVolum.to_csv('carCommentVolum.csv')
newsReplyVolum.to_csv('newsReplyVolum.csv')
salesVolume['salesVolume']=salesVolume['salesVolume'].astype(int)
salesVolume.to_csv('salesVolume.csv')


In [116]:
te1 = salesVolume.rename(columns={'salesVolume':'forecastVolum'})
te1['group']='A'

In [53]:
te2 = te1.merge(train_sales_data[['province','adcode','model','bodyType']].drop_duplicates(),on=['province','model'])

In [58]:
evaluation_public

id province  adcode             model  regYear  regMonth  \
0        1       上海  310000  3c974920a76ac9c1     2018         1   
1        2       云南  530000  3c974920a76ac9c1     2018         1   
2        3      内蒙古  150000  3c974920a76ac9c1     2018         1   
3        4       北京  110000  3c974920a76ac9c1     2018         1   
4        5       四川  510000  3c974920a76ac9c1     2018         1   
5        6       安徽  340000  3c974920a76ac9c1     2018         1   
6        7       山东  370000  3c974920a76ac9c1     2018         1   
7        8       山西  140000  3c974920a76ac9c1     2018         1   
8        9       广东  440000  3c974920a76ac9c1     2018         1   
9       10       广西  450000  3c974920a76ac9c1     2018         1   
10      11       江苏  320000  3c974920a76ac9c1     2018         1   
11      12       江西  360000  3c974920a76ac9c1     2018         1   
12      13       河北  130000  3c974920a76ac9c1     2018         1   
13      14       河南  410000  3c974920a76ac9c1     2018         1   
14      15       浙江  330000  3c974920a76ac9c1     2018         1   
15      16       湖北  420000  3c974920a76ac9c1     2018         1   
16      17       湖南  430000  3c974920a76ac9c1     2018         1   
17      18       福建  350000  3c974920a76ac9c1     2018         1   
18      19       辽宁  210000  3c974920a76ac9c1     2018         1   
19      20       重庆  500000  3c974920a76ac9c1     2018         1   
20      21       陕西  610000  3c974920a76ac9c1     2018         1   
21      22      黑龙江  230000  3c974920a76ac9c1     2018         1   
22      23       上海  310000  3d7554f1f56dd664     2018         1   
23      24       云南  530000  3d7554f1f56dd664     2018         1   
24      25      内蒙古  150000  3d7554f1f56dd664     2018         1   
25      26       北京  110000  3d7554f1f56dd664     2018         1   
26      27       四川  510000  3d7554f1f56dd664     2018         1   
27      28       安徽  340000  3d7554f1f56dd664     2018         1   
28      29       山东  370000  3d7554f1f56dd664     2018         1   
29      30       山西  140000  3d7554f1f56dd664     2018         1   
...    ...      ...     ...               ...      ...       ...   
5250  5339       浙江  330000  c6cd4e0e073f5ac2     2018         4   
5251  5340       湖北  420000  c6cd4e0e073f5ac2     2018         4   
5252  5341       湖南  430000  c6cd4e0e073f5ac2     2018         4   
5253  5342       福建  350000  c6cd4e0e073f5ac2     2018         4   
5254  5343       辽宁  210000  c6cd4e0e073f5ac2     2018         4   
5255  5344       重庆  500000  c6cd4e0e073f5ac2     2018         4   
5256  5345       陕西  610000  c6cd4e0e073f5ac2     2018         4   
5257  5346      黑龙江  230000  c6cd4e0e073f5ac2     2018         4   
5258  5347       上海  310000  a9a43d1a7ecbe75d     2018         4   
5259  5348       云南  530000  a9a43d1a7ecbe75d     2018         4   
5260  5349      内蒙古  150000  a9a43d1a7ecbe75d     2018         4   
5261  5350       北京  110000  a9a43d1a7ecbe75d     2018         4   
5262  5351       四川  510000  a9a43d1a7ecbe75d     2018         4   
5263  5352       安徽  340000  a9a43d1a7ecbe75d     2018         4   
5264  5353       山东  370000  a9a43d1a7ecbe75d     2018         4   
5265  5354       山西  140000  a9a43d1a7ecbe75d     2018         4   
5266  5355       广东  440000  a9a43d1a7ecbe75d     2018         4   
5267  5356       广西  450000  a9a43d1a7ecbe75d     2018         4   
5268  5357       江苏  320000  a9a43d1a7ecbe75d     2018         4   
5269  5358       江西  360000  a9a43d1a7ecbe75d     2018         4   
5270  5359       河北  130000  a9a43d1a7ecbe75d     2018         4   
5271  5360       河南  410000  a9a43d1a7ecbe75d     2018         4   
5272  5361       浙江  330000  a9a43d1a7ecbe75d     2018         4   
5273  5362       湖北  420000  a9a43d1a7ecbe75d     2018         4   
5274  5363       湖南  430000  a9a43d1a7ecbe75d     2018         4   
5275  5364       福建  350000  a9a43d1a7ecbe75d     2018         4   
5276  5365       辽宁  210000  a9a43d1a7ecbe75d     2018         4

In [61]:
res1 = te2.merge(evaluation_public[['province','adcode','model','regYear','regMonth','id']],on=['province','adcode','model','regYear','regMonth'])

In [67]:
resss = res1.sort_values('id')[['id','group','province','adcode','model','bodyType','regYear','regMonth','forecastVolum']].set_index('id')

In [96]:
df2['salesVolume'].min()

2

In [78]:

resss['forecastVolum']=resss['forecastVolum'].abs()
resss['forecastVolum'] = resss['forecastVolum']+2
resss

In [141]:
evaluation_public.columns

Index(['id', 'province', 'adcode', 'model', 'regYear', 'regMonth',
       'forecastVolum'],
      dtype='object')

In [143]:
res2 = evaluation_public[['id', 'province', 'adcode', 'model', 'regYear', 'regMonth']].merge(resss,on=['province','adcode','model','regYear','regMonth'])

In [147]:
res2[['id','forecastVolum']].to_csv('res2.csv',index=False)

In [135]:
resss.reset_index()

id group province  adcode             model bodyType  regYear  \
0        1     A       上海  310000  3c974920a76ac9c1      SUV     2018   
1        2     A       云南  530000  3c974920a76ac9c1      SUV     2018   
2        3     A      内蒙古  150000  3c974920a76ac9c1      SUV     2018   
3        4     A       北京  110000  3c974920a76ac9c1      SUV     2018   
4        5     A       四川  510000  3c974920a76ac9c1      SUV     2018   
5        6     A       安徽  340000  3c974920a76ac9c1      SUV     2018   
6        7     A       山东  370000  3c974920a76ac9c1      SUV     2018   
7        8     A       山西  140000  3c974920a76ac9c1      SUV     2018   
8        9     A       广东  440000  3c974920a76ac9c1      SUV     2018   
9       10     A       广西  450000  3c974920a76ac9c1      SUV     2018   
10      11     A       江苏  320000  3c974920a76ac9c1      SUV     2018   
11      12     A       江西  360000  3c974920a76ac9c1      SUV     2018   
12      13     A       河北  130000  3c974920a76ac9c1      SUV     2018   
13      14     A       河南  410000  3c974920a76ac9c1      SUV     2018   
14      15     A       浙江  330000  3c974920a76ac9c1      SUV     2018   
15      16     A       湖北  420000  3c974920a76ac9c1      SUV     2018   
16      17     A       湖南  430000  3c974920a76ac9c1      SUV     2018   
17      18     A       福建  350000  3c974920a76ac9c1      SUV     2018   
18      19     A       辽宁  210000  3c974920a76ac9c1      SUV     2018   
19      20     A       重庆  500000  3c974920a76ac9c1      SUV     2018   
20      21     A       陕西  610000  3c974920a76ac9c1      SUV     2018   
21      22     A      黑龙江  230000  3c974920a76ac9c1      SUV     2018   
22      23     A       上海  310000  3d7554f1f56dd664    Sedan     2018   
23      24     A       云南  530000  3d7554f1f56dd664    Sedan     2018   
24      25     A      内蒙古  150000  3d7554f1f56dd664    Sedan     2018   
25      26     A       北京  110000  3d7554f1f56dd664    Sedan     2018   
26      27     A       四川  510000  3d7554f1f56dd664    Sedan     2018   
27      28     A       安徽  340000  3d7554f1f56dd664    Sedan     2018   
28      29     A       山东  370000  3d7554f1f56dd664    Sedan     2018   
29      30     A       山西  140000  3d7554f1f56dd664    Sedan     2018   
...    ...   ...      ...     ...               ...      ...      ...   
5250  5339     A       浙江  330000  c6cd4e0e073f5ac2    Sedan     2018   
5251  5340     A       湖北  420000  c6cd4e0e073f5ac2    Sedan     2018   
5252  5341     A       湖南  430000  c6cd4e0e073f5ac2    Sedan     2018   
5253  5342     A       福建  350000  c6cd4e0e073f5ac2    Sedan     2018   
5254  5343     A       辽宁  210000  c6cd4e0e073f5ac2    Sedan     2018   
5255  5344     A       重庆  500000  c6cd4e0e073f5ac2    Sedan     2018   
5256  5345     A       陕西  610000  c6cd4e0e073f5ac2    Sedan     2018   
5257  5346     A      黑龙江  230000  c6cd4e0e073f5ac2    Sedan     2018   
5258  5347     A       上海  310000  a9a43d1a7ecbe75d      SUV     2018   
5259  5348     A       云南  530000  a9a43d1a7ecbe75d      SUV     2018   
5260  5349     A      内蒙古  150000  a9a43d1a7ecbe75d      SUV     2018   
5261  5350     A       北京  110000  a9a43d1a7ecbe75d      SUV     2018   
5262  5351     A       四川  510000  a9a43d1a7ecbe75d      SUV     2018   
5263  5352     A       安徽  340000  a9a43d1a7ecbe75d      SUV     2018   
5264  5353     A       山东  370000  a9a43d1a7ecbe75d      SUV     2018   
5265  5354     A       山西  140000  a9a43d1a7ecbe75d      SUV     2018   
5266  5355     A       广东  440000  a9a43d1a7ecbe75d      SUV     2018   
5267  5356     A       广西  450000  a9a43d1a7ecbe75d      SUV     2018   
5268  5357     A       江苏  320000  a9a43d1a7ecbe75d      SUV     2018   
5269  5358     A       江西  360000  a9a43d1a7ecbe75d      SUV     2018   
5270  5359     A       河北  130000  a9a43d1a7ecbe75d      SUV     2018   
5271  5360     A       河南  410000  a9a43d1a7ecbe75d      SUV     2018   
5272  5361     A       浙江  330000  a9a43d1a7ecbe75d      SUV     2

In [113]:
resss.drop(['group','bodyType'],axis=1).to_csv('res_prophet.csv',encoding='utf-8')

In [118]:
resss.to_csv('res_prophet_groupA.csv',encoding='utf-8')

In [54]:
score['regMonth'] = score['ds'].apply(lambda x:x.month)

In [57]:
score

ds        yhat  yhat_lower  yhat_upper       score  regYear  \
24 2018-01-31  269.828406  200.377178  334.884006  281.081275     2018   
25 2018-02-28  298.961156  222.754943  366.737365  309.144396     2018   
26 2018-03-31  263.976148  194.198414  338.000631  280.479744     2018   
27 2018-04-30  273.153559  202.378379  339.706027  284.774967     2018   

    regMonth  
24         1  
25         2  
26         3  
27         4

In [30]:
evaluation_public.head()

id province  adcode             model  regYear  regMonth  forecastVolum
0   1       上海  310000  3c974920a76ac9c1     2018         1            NaN
1   2       云南  530000  3c974920a76ac9c1     2018         1            NaN
2   3      内蒙古  150000  3c974920a76ac9c1     2018         1            NaN
3   4       北京  110000  3c974920a76ac9c1     2018         1            NaN
4   5       四川  510000  3c974920a76ac9c1     2018         1            NaN

In [63]:
carCommentVolum =ProphetPredit(df2,'carCommentVolum',evaluation_public).main()

/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Ru

上海 3c974920a76ac9c1 Predict Done Result:288.0......


/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Ru

上海 3d7554f1f56dd664 Predict Done Result:1370.0......


/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Ru

...

黑龙江 d0f245b8781e3631 Predict Done Result:261.0......


/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Ru

黑龙江 c6cd4e0e073f5ac2 Predict Done Result:456.0......


/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Ru

黑龙江 a9a43d1a7ecbe75d Predict Done Result:364.0......


In [64]:
newsReplyVolum =ProphetPredit(df2,'newsReplyVolum',evaluation_public).main()

/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Ru

上海 3c974920a76ac9c1 Predict Done Result:1790.0......


/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Ru

上海 3d7554f1f56dd664 Predict Done Result:2830.0......


/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Ru

...

黑龙江 f270f6a489c6a9d7 Predict Done Result:257.0......


/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Ru

黑龙江 d0f245b8781e3631 Predict Done Result:4720.0......


/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/Users/sn0wfree/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling weekly seasonality. Run prophet with weekly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Ru

黑龙江 c6cd4e0e073f5ac2 Predict Done Result:995.0......
黑龙江 a9a43d1a7ecbe75d Predict Done Result:3570.0......


In [72]:
newsReplyVolum.rename(columns={'forecastVolum':'newsReplyVolum'}).to_csv('newsReplyVolum.csv')

In [73]:
carCommentVolum.rename(columns={'forecastVolum':'carCommentVolum'}).to_csv('carCommentVolum.csv')
# carCommentVolum.to_csv('carCommentVolum.csv')

In [76]:
carCommentVolum.rename(columns={'forecastVolum':'carCommentVolum'})

id province  adcode             model  regYear  regMonth  \
0        1       上海  310000  3c974920a76ac9c1     2018         1   
1        2       云南  530000  3c974920a76ac9c1     2018         1   
2        3      内蒙古  150000  3c974920a76ac9c1     2018         1   
3        4       北京  110000  3c974920a76ac9c1     2018         1   
4        5       四川  510000  3c974920a76ac9c1     2018         1   
5        6       安徽  340000  3c974920a76ac9c1     2018         1   
6        7       山东  370000  3c974920a76ac9c1     2018         1   
7        8       山西  140000  3c974920a76ac9c1     2018         1   
8        9       广东  440000  3c974920a76ac9c1     2018         1   
9       10       广西  450000  3c974920a76ac9c1     2018         1   
10      11       江苏  320000  3c974920a76ac9c1     2018         1   
11      12       江西  360000  3c974920a76ac9c1     2018         1   
12      13       河北  130000  3c974920a76ac9c1     2018         1   
13      14       河南  410000  3c974920a76ac9c1     2018         1   
14      15       浙江  330000  3c974920a76ac9c1     2018         1   
15      16       湖北  420000  3c974920a76ac9c1     2018         1   
16      17       湖南  430000  3c974920a76ac9c1     2018         1   
17      18       福建  350000  3c974920a76ac9c1     2018         1   
18      19       辽宁  210000  3c974920a76ac9c1     2018         1   
19      20       重庆  500000  3c974920a76ac9c1     2018         1   
20      21       陕西  610000  3c974920a76ac9c1     2018         1   
21      22      黑龙江  230000  3c974920a76ac9c1     2018         1   
22      23       上海  310000  3d7554f1f56dd664     2018         1   
23      24       云南  530000  3d7554f1f56dd664     2018         1   
24      25      内蒙古  150000  3d7554f1f56dd664     2018         1   
25      26       北京  110000  3d7554f1f56dd664     2018         1   
26      27       四川  510000  3d7554f1f56dd664     2018         1   
27      28       安徽  340000  3d7554f1f56dd664     2018         1   
28      29       山东  370000  3d7554f1f56dd664     2018         1   
29      30       山西  140000  3d7554f1f56dd664     2018         1   
...    ...      ...     ...               ...      ...       ...   
5250  5339       浙江  330000  c6cd4e0e073f5ac2     2018         4   
5251  5340       湖北  420000  c6cd4e0e073f5ac2     2018         4   
5252  5341       湖南  430000  c6cd4e0e073f5ac2     2018         4   
5253  5342       福建  350000  c6cd4e0e073f5ac2     2018         4   
5254  5343       辽宁  210000  c6cd4e0e073f5ac2     2018         4   
5255  5344       重庆  500000  c6cd4e0e073f5ac2     2018         4   
5256  5345       陕西  610000  c6cd4e0e073f5ac2     2018         4   
5257  5346      黑龙江  230000  c6cd4e0e073f5ac2     2018         4   
5258  5347       上海  310000  a9a43d1a7ecbe75d     2018         4   
5259  5348       云南  530000  a9a43d1a7ecbe75d     2018         4   
5260  5349      内蒙古  150000  a9a43d1a7ecbe75d     2018         4   
5261  5350       北京  110000  a9a43d1a7ecbe75d     2018         4   
5262  5351       四川  510000  a9a43d1a7ecbe75d     2018         4   
5263  5352       安徽  340000  a9a43d1a7ecbe75d     2018         4   
5264  5353       山东  370000  a9a43d1a7ecbe75d     2018         4   
5265  5354       山西  140000  a9a43d1a7ecbe75d     2018         4   
5266  5355       广东  440000  a9a43d1a7ecbe75d     2018         4   
5267  5356       广西  450000  a9a43d1a7ecbe75d     2018         4   
5268  5357       江苏  320000  a9a43d1a7ecbe75d     2018         4   
5269  5358       江西  360000  a9a43d1a7ecbe75d     2018         4   
5270  5359       河北  130000  a9a43d1a7ecbe75d     2018         4   
5271  5360       河南  410000  a9a43d1a7ecbe75d     2018         4   
5272  5361       浙江  330000  a9a43d1a7ecbe75d     2018         4   
5273  5362       湖北  420000  a9a43d1a7ecbe75d     2018         4   
5274  5363       湖南  430000  a9a43d1a7ecbe75d     2018         4   
5275  5364       福建  350000  a9a43d1a7ecbe75d     2018         4   
5276  5365       辽宁  210000  a9a43d1a7ecbe75d     2018         4

In [71]:
df2[(df2['model']=='3c974920a76ac9c1')&(df2['province']=='上海')]

province             model  regYear  regMonth  salesVolume  popularity  \
0           上海  3c974920a76ac9c1     2016         1          292        1479   
1320        上海  3c974920a76ac9c1     2016         2          134        2355   
2640        上海  3c974920a76ac9c1     2016         3          323        1794   
3960        上海  3c974920a76ac9c1     2016         4          266        1260   
5280        上海  3c974920a76ac9c1     2016         5          271        1148   
6600        上海  3c974920a76ac9c1     2016         6          235        1083   
7920        上海  3c974920a76ac9c1     2016         7          260        1171   
9240        上海  3c974920a76ac9c1     2016         8          162        1235   
10560       上海  3c974920a76ac9c1     2016         9          265        1417   
11880       上海  3c974920a76ac9c1     2016        10          228        1447   
13200       上海  3c974920a76ac9c1     2016        11          369        1165   
14520       上海  3c974920a76ac9c1     2016        12          374        1161   
15840       上海  3c974920a76ac9c1     2017         1          305        1072   
17160       上海  3c974920a76ac9c1     2017         2          193        1306   
18480       上海  3c974920a76ac9c1     2017         3          309         850   
19800       上海  3c974920a76ac9c1     2017         4          264         628   
21120       上海  3c974920a76ac9c1     2017         5          241         636   
22440       上海  3c974920a76ac9c1     2017         6          251         511   
23760       上海  3c974920a76ac9c1     2017         7          240         540   
25080       上海  3c974920a76ac9c1     2017         8          298         586   
26400       上海  3c974920a76ac9c1     2017         9          308         571   
27720       上海  3c974920a76ac9c1     2017        10          270         725   
29040       上海  3c974920a76ac9c1     2017        11          286         580   
30360       上海  3c974920a76ac9c1     2017        12          312         602   

       carCommentVolum  newsReplyVolum       ym  
0                   11             106  2016-01  
1320                 6            2255  2016-02  
2640                13             861  2016-03  
3960                16             105  2016-04  
5280                28            2107  2016-05  
6600                30            2957  2016-06  
7920                37           13106  2016-07  
9240                74            1100  2016-08  
10560              221             882  2016-09  
11880              216            2543  2016-10  
13200              150            1228  2016-11  
14520              117            2113  2016-12  
15840              158            1737  2017-01  
17160              187            1562  2017-02  
18480              186             993  2017-03  
19800              148            2259  2017-04  
21120              194            1623  2017-05  
22440              175             788  2017-06  
23760              149             414  2017-07  
25080              328             654  2017-08  
26400              252            1283  2017-09  
27720              214             292  2017-10  
29040              148            3142  2017-11  
30360              129             272  2017-12

In [78]:
newsReplyVolum

id province  adcode             model  regYear  regMonth  \
0        1       上海  310000  3c974920a76ac9c1     2018         1   
1        2       云南  530000  3c974920a76ac9c1     2018         1   
2        3      内蒙古  150000  3c974920a76ac9c1     2018         1   
3        4       北京  110000  3c974920a76ac9c1     2018         1   
4        5       四川  510000  3c974920a76ac9c1     2018         1   
5        6       安徽  340000  3c974920a76ac9c1     2018         1   
6        7       山东  370000  3c974920a76ac9c1     2018         1   
7        8       山西  140000  3c974920a76ac9c1     2018         1   
8        9       广东  440000  3c974920a76ac9c1     2018         1   
9       10       广西  450000  3c974920a76ac9c1     2018         1   
10      11       江苏  320000  3c974920a76ac9c1     2018         1   
11      12       江西  360000  3c974920a76ac9c1     2018         1   
12      13       河北  130000  3c974920a76ac9c1     2018         1   
13      14       河南  410000  3c974920a76ac9c1     2018         1   
14      15       浙江  330000  3c974920a76ac9c1     2018         1   
15      16       湖北  420000  3c974920a76ac9c1     2018         1   
16      17       湖南  430000  3c974920a76ac9c1     2018         1   
17      18       福建  350000  3c974920a76ac9c1     2018         1   
18      19       辽宁  210000  3c974920a76ac9c1     2018         1   
19      20       重庆  500000  3c974920a76ac9c1     2018         1   
20      21       陕西  610000  3c974920a76ac9c1     2018         1   
21      22      黑龙江  230000  3c974920a76ac9c1     2018         1   
22      23       上海  310000  3d7554f1f56dd664     2018         1   
23      24       云南  530000  3d7554f1f56dd664     2018         1   
24      25      内蒙古  150000  3d7554f1f56dd664     2018         1   
25      26       北京  110000  3d7554f1f56dd664     2018         1   
26      27       四川  510000  3d7554f1f56dd664     2018         1   
27      28       安徽  340000  3d7554f1f56dd664     2018         1   
28      29       山东  370000  3d7554f1f56dd664     2018         1   
29      30       山西  140000  3d7554f1f56dd664     2018         1   
...    ...      ...     ...               ...      ...       ...   
5250  5339       浙江  330000  c6cd4e0e073f5ac2     2018         4   
5251  5340       湖北  420000  c6cd4e0e073f5ac2     2018         4   
5252  5341       湖南  430000  c6cd4e0e073f5ac2     2018         4   
5253  5342       福建  350000  c6cd4e0e073f5ac2     2018         4   
5254  5343       辽宁  210000  c6cd4e0e073f5ac2     2018         4   
5255  5344       重庆  500000  c6cd4e0e073f5ac2     2018         4   
5256  5345       陕西  610000  c6cd4e0e073f5ac2     2018         4   
5257  5346      黑龙江  230000  c6cd4e0e073f5ac2     2018         4   
5258  5347       上海  310000  a9a43d1a7ecbe75d     2018         4   
5259  5348       云南  530000  a9a43d1a7ecbe75d     2018         4   
5260  5349      内蒙古  150000  a9a43d1a7ecbe75d     2018         4   
5261  5350       北京  110000  a9a43d1a7ecbe75d     2018         4   
5262  5351       四川  510000  a9a43d1a7ecbe75d     2018         4   
5263  5352       安徽  340000  a9a43d1a7ecbe75d     2018         4   
5264  5353       山东  370000  a9a43d1a7ecbe75d     2018         4   
5265  5354       山西  140000  a9a43d1a7ecbe75d     2018         4   
5266  5355       广东  440000  a9a43d1a7ecbe75d     2018         4   
5267  5356       广西  450000  a9a43d1a7ecbe75d     2018         4   
5268  5357       江苏  320000  a9a43d1a7ecbe75d     2018         4   
5269  5358       江西  360000  a9a43d1a7ecbe75d     2018         4   
5270  5359       河北  130000  a9a43d1a7ecbe75d     2018         4   
5271  5360       河南  410000  a9a43d1a7ecbe75d     2018         4   
5272  5361       浙江  330000  a9a43d1a7ecbe75d     2018         4   
5273  5362       湖北  420000  a9a43d1a7ecbe75d     2018         4   
5274  5363       湖南  430000  a9a43d1a7ecbe75d     2018         4   
5275  5364       福建  350000  a9a43d1a7ecbe75d     2018         4   
5276  5365       辽宁  210000  a9a43d1a7ecbe75d     2018         4